In [ ]:
# Import the required packages
import ipyvuetify as v
import pandas as pd

In [ ]:
# Widgets
app = v.App()

image = v.Img(
    lazy_src="https://seeq.com/sites/default/files/seeq-content/seeq-logo-blue-web-33h.svg",
    aspect_ratio="16/9",
    width=100,
    src="https://seeq.com/sites/default/files/seeq-content/seeq-logo-blue-web-33h.svg",
)
message = v.Text(
    children=["Seeq Data Lab Add-on Tool!"],
    style_="font-size:25px"
)

header = v.Container(children=[image,message])

url_input = v.TextField(label='Workbench URL', v_model=None)

execute_button = v.Btn(
    button_style='success',
    children=['Get Signals']
)


items_dropdown = v.Select(item_text='Name', 
                          item_value='ID', 
                          label="Select Signal", 
                          v_model=None, 
                          return_object=True
                         )
items_dropdown.disabled = True

add_5_checkbox = v.Checkbox(label='Add 5', v_model=False)
add_5_checkbox.disabled = True

multiply_3_checkbox = v.Checkbox(label='Multiply by 3', v_model=False)
multiply_3_checkbox.disabled = True

submit_button = v.Btn(
    button_style='success',
    children=['Submit'])
submit_button.disabled = True

input_container = v.Container(children=[url_input,
                                        execute_button,
                                        items_dropdown,
                                        add_5_checkbox,
                                        multiply_3_checkbox,
                                       submit_button])



In [ ]:
#  Actions
def get_worksheet_items(*args):
   
    #Get Items on worksheet
    execute_button.loading = True
    items = spy.search(url_input.v_model, quiet=True)
    signals = items.loc[items.Type.str.contains('Signal')]
    dropdown_items = list(signals[['Name','ID']].T.to_dict().values())
    items_dropdown.items = dropdown_items
    items_dropdown.select = dropdown_items[0]
    items_dropdown.disabled=False
    submit_button.disabled=False
    add_5_checkbox.disabled=False
    multiply_3_checkbox.disabled=False
    execute_button.loading = False

    
def submit_formula(*args):
    submit_button.loading = True
    name = f"{items_dropdown.v_model['Name']}"
    workbook_id = spy.utils.get_workbook_id_from_url(url_input.v_model)
    worksheet_id = spy.utils.get_worksheet_id_from_url(url_input.v_model)
    ws = spy.search({'ID':worksheet_id}, quiet=True)
    worksheet_name = ws['Name'].iloc[0]
    formula = "$s"
    same_name = True
    if multiply_3_checkbox.v_model:
        formula += ".multiply(3)"
        name +=' x3 '
        same_name = False
    if add_5_checkbox.v_model:
        formula += ".add(5)"
        name +=' +5'
        same_name = False
    if same_name :
        name +=' Copy'
    current_signals = spy.search(url_input.v_model, quiet=True)
    new_signal = pd.DataFrame([{
    'Name': name,
    'Type': 'Signal',
    'Formula': formula,
    'Formula Parameters': {
        '$s': items_dropdown.v_model['ID']
    }
    }])
    metadata = pd.concat([current_signals, new_signal]).reset_index(drop=True)
    metadata = metadata.drop_duplicates(subset=['ID'])
    spy.push(metadata=metadata[['Name','Type','ID','Formula','Formula Parameters']], 
             workbook=workbook_id, 
             worksheet=worksheet_id,
             errors='catalog',
             quiet=True)
    submit_button.loading=False
    

execute_button.on_event('click',get_worksheet_items)
submit_button.on_event('click', submit_formula)

In [ ]:
# Output 
app.children=[
        header,
        input_container
    ]
app